# MOLEARN ANALYSIS TUTORIAL

In [ ]:
THIS SCRIPT IS USED TO GET RMSD AND DOPE OF THE WHOLE DATASET, NOT SPLIT IN TRAINING AND VALIDATION

## Introduction

[molearn](https://github.com/Degiacomi-Lab/molearn) is a Python package streamlining the implementation of machine learning models trainable on protein conformational spaces. This tutorial is dedicated to demonstrating the first principles of analysing the performance of a trained neural network. Implementations of what described below is available in the `MolearnAnalysis` class. You can find out how to use this class in the [molearn_GUI.ipynb](molearn_GUI.ipynb) notebook.

This tutorial is divided in the following sections:

[1. Load neural network and training set](#ref1)
   - [1.1. The data](#ref11)
   - [1.2. Data loading](#ref12)
   - [1.3. Loading the neural network](#ref13)
   
   
[2. Projection into latent space and back](#ref2)
 
 
[3. Dataset analysis](#ref3)
   -  [3.1. RMSD (or MSE) of input vs autoencoded](#ref31)
   -  [3.2. DOPE score of input vs autoencoded](#ref32)
   
   
[4. Full latent space characterization](#ref4)
   - [4.1. Evaluate re-encoding error](#ref41)
   - [4.2. Evaluate DOPE score](#ref42)

To get started, let's load some packages!

In [1]:
import sys, os, glob
from copy import deepcopy

import numpy as np
import matplotlib.pyplot as plt

import torch.nn as nn
import torch.nn.functional as F
import torch.optim

import nglview as nv
import MDAnalysis as mda
import warnings
warnings.filterwarnings("ignore")

import modeller
from modeller import *
from modeller.scripts import complete_pdb

import biobox as bb

from tqdm import tqdm
#edit path as required for your computer (or remove, if you installed molearn via conda-forge)
sys.path.insert(0, f"C:{os.sep}Users{os.sep}xdzl45{os.sep}workspace{os.sep}molearn{os.sep}src") 

import molearn
from molearn.models.foldingnet import AutoEncoder
device = torch.device('cuda') if torch.cuda.is_available() else torch.device('cpu')

import pandas as pd


## 1. Load neural network and training set <a class="anchor" id="ref1"></a>

### 1.1. the data <a class="anchor" id="ref11"></a>

MurD is a 47-kDa ATP-driven ligase responsible for the biosynthesis of a bacterial peptidoglycan precursor (UDP-N-acetylmuramoyl-L-alanyl-D-glutamate). When bound to its ligand, UDP-N-acetylmuramoyl-L-alanyl-D-alanine, MurD is stabilized in a closed conformation (PDB: [3UAG](https://www.rcsb.org/structure/3UAG)). In the absence of UDP-N-acetylmuramoyl-L-alanyl-D-alanine, MurD takes instead an open conformation (PDB: [1E0D](https://www.rcsb.org/structure/1E0D)). We have carried out molecular dynamics simulations of both states. For this tutorial, we will load a multi-PDB file containing a subset of conformations of both trajectories.

Let's start by defining the files containing the training set (variable `open_file` and `closed_file`), and test set (variable `test_set_file`).

The open_file and closed_file contain training set MD simulations of the closed and open states.

By taking the closed conformation and manually removing the ligand, the protein switches to an open conformation. This is the simulation we will used as test set.

### 1.2. data loading <a class="anchor" id="ref12"></a>

We will now prepare the training set, transforming into a `torch.Tensor` making sure to extract from it only the atoms actually used during neural network training (CA, C, N, O, CB). The following cell yields a PDBData class with attributes:
 - `PDBData.dataset`, a pyTorch `Tensor` containing a desired subset of *normalized* atomic coordinates ready for submission to the neural network.
 - `PDBData.mean` and `PDBData.std`, the mean and standard deviation of the original input data, useful to rescale generated structures into atomic coordinates.
 - `PDBData.get_atominfo()` method that returns a list containing the names, resid, and resname of atoms in the training set (in the same order)
 - `PDBData.mol`, a  `biobox` instance corresponding to the coordinates in `PDBData.dataset`, useful as a PDB writer and offering useful helper functions, e.g. RMSD calculation.


In [2]:
data = molearn.PDBData()
data.import_pdb('alignToProteinH.pdb')
#data.import_pdb(closed_file) # this will append closed_file structures onto open_files
data.atomselect(atoms=['CA', 'C', 'CB', 'N', 'O'])
data.prepare_dataset()

training_set = data.dataset
stdval = data.std
meanval = data.mean
mol = data.mol
atom_names = data.get_atominfo()

Dataset.shape: torch.Size([1427, 3, 308])
mean: 77.27854769413021, std: 27.365156008484128


`training_set` takes the form of a Nx3xM normalised `Tensor` object, where N is the number of examples, M the number of atoms, and 3 the x, y, z coordinates of each atom. This is the order of dimensions required by the neural network, a typical multiPDB has columns in the NxMx3 order.

In [3]:
print(training_set.shape)

torch.Size([1427, 3, 308])


Let's now load the test set in the same way as the training set. This time, we will only retain the coordinates of atoms, normalised and ready to be submitted to the neural network (discarding all other outputs). The test set must contain the same atoms as the training set, in the same order. The two datasets should also be aligned, since *molearn* is not rototranslation invariant.

### 1.3. loading the neural network <a class="anchor" id="ref13"></a>

We can now load the parameters of a trained neural network saved in the following file (variable `networkfile`):

In [4]:
networkfile = f'../run1_alignToProteinH_foldingnet_checkpoint/checkpoint_epoch83_loss-3.5729515586100833.ckpt'
#network_file = sorted(glob("run1*ProteinH*/checkpoint_epoch83_loss-3.5729515586100833.ckpt"))[0]

Note that the parameters passed to the `AutoEncoder` costructor need to be the same as those used to build the trained neural network.

In [5]:
checkpoint = torch.load(networkfile, map_location=device)

network = AutoEncoder(**checkpoint['network_kwargs'])
network.load_state_dict(checkpoint['model_state_dict'])

network.eval()

AutoEncoder(
  (encoder): Encoder(
    (conv1): Conv1d(12, 64, kernel_size=(1,), stride=(1,))
    (conv2): Conv1d(64, 64, kernel_size=(1,), stride=(1,))
    (conv3): Conv1d(64, 64, kernel_size=(1,), stride=(1,))
    (bn1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (bn2): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (bn3): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (graph_layer1): GraphLayer(
      (conv): Conv1d(64, 128, kernel_size=(1,), stride=(1,))
      (bn): BatchNorm1d(128, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    )
    (graph_layer2): GraphLayer(
      (conv): Conv1d(128, 1024, kernel_size=(1,), stride=(1,))
      (bn): BatchNorm1d(1024, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    )
    (conv4): Conv1d(1024, 512, kernel_size=(1,), stride=(1,))
    (bn4): BatchNorm1d(512, eps=1e-05, momentum=0.1, affine=True, 

In [6]:
print(next(network.parameters()))

Parameter containing:
tensor([[[-0.2173],
         [-0.0774],
         [ 0.3027],
         [ 0.1390],
         [-0.0537],
         [ 0.1045],
         [ 0.0282],
         [-0.2315],
         [ 0.0760],
         [ 0.3616],
         [-0.1626],
         [-0.1182]],

        [[-0.1796],
         [-0.1569],
         [ 0.0656],
         [-0.2291],
         [-0.1529],
         [-0.1962],
         [-0.1315],
         [-0.0294],
         [ 0.1930],
         [ 0.0675],
         [-0.2866],
         [ 0.0453]],

        [[ 0.2346],
         [ 0.1605],
         [-0.1149],
         [ 0.0373],
         [-0.2561],
         [-0.3547],
         [-0.4433],
         [ 0.4325],
         [-0.3814],
         [-0.1184],
         [-0.0129],
         [ 0.4913]],

        [[-0.1032],
         [ 0.0084],
         [-0.0603],
         [ 0.5875],
         [ 0.1786],
         [-0.2617],
         [-0.0665],
         [ 0.2785],
         [-0.0375],
         [ 0.1876],
         [ 0.2565],
         [-0.0050]],

        [[

## 2. Projection into latent space and back <a class="anchor" id="ref2"></a>

Let's start by projecting the whole training set into the latent space. Due to memory constraints we often can't simply encode or decode the entire dataset in one go like:
```
with torch.no_grad():
    z = network.encode(training_set.float())
```
We will need to do this in batches instead.

In [7]:
BATCH_SIZE = 8

def batched_encode(dataset):
    # Preallocate space for the results to go
    z = torch.empty(dataset.shape[0], 2, 1, dtype=dataset.dtype, device = dataset.device)
    with torch.no_grad():
        for i in tqdm(range(0, z.shape[0], BATCH_SIZE)):
            z[i:i+BATCH_SIZE] = network.encode(dataset[i:i+BATCH_SIZE].float())
    return z

def batched_decode(latent_vector, n_atoms):
    decoded = torch.empty(latent_vector.shape[0], 3, n_atoms, dtype=latent_vector.dtype, device = latent_vector.device)
    with torch.no_grad():
        for i in tqdm(range(0, decoded.shape[0], BATCH_SIZE)):
            decoded[i:i+BATCH_SIZE] = network.decode(latent_vector[i:i+BATCH_SIZE].float())[:,:,:n_atoms]
    return decoded

`z` is a (Nx2x1) `Tensor` object, featuring the projection in the latent space of each of the N examples in the training set. If this notebook is running in a computer with a GPU, it will be stored in its memory. To get the data so we can plot it, we should move it back to the CPU, and remove one dimension.

`z` can be decoded back into structures that, hopefully, will closely resemble the training set. Note that we will have to clip the output to the size of dataset's degrees of freedom (an extra padding is present). As for the encoding part, while in principle it is possible to decode all the encoded training set in one shot as follows

```
with torch.no_grad():  
    decoded_training = network.decode(z)[:, :, :training_set.shape[2]]
```
it is often impossible to do so owing to memory constraints. Let's decode our dateset in batches!

`decoded_training` is a now `Tensor` object stored in the GPU with the same dimensionality as the input `training_set`, and features normalised atomic coordinates. While it can already be directly compared with `training_set`, to obtain an actual protein structure we can observe, we should reorder the columns, move the data onto the CPU and "un-normalise" them.

Ok, now let's repeat encoding and decoding with the test set!

## 3. dataset analysis <a class="anchor" id="ref3"></a>

### 3.1. RMSD (or MSE) of input vs autoencoded <a class="anchor" id="ref31"></a>

A way to evaluate the performance of the network, is to compare protein conformations before they are submitted to the neural network, and after they get encoded and decoded. Note that reporting such results for the training set only is poor practice, an independent test set should be submitted to evaluate the ability of the network to generalize beyond the examples provided for training. Let's calculate the MSE of both training and test sets!

In [8]:
import csv
def get_error(network, dataset, meanval, stdval, align=False, mol=""):
    '''
    Calculate the reconstruction error of a dataset encoded and decoded by a trained neural network
    '''

    #z = network.encode(dataset.float())
    z = batched_encode(dataset.float())
    #decoded = network.decode(z)[:,:,:dataset.shape[2]]
    decoded = batched_decode(z, dataset.shape[2])
    err = []
    for i in tqdm(range(dataset.shape[0])):

        crd_ref = dataset[i].permute(1,0).unsqueeze(0).data.cpu().numpy()*stdval + meanval
        crd_mdl = decoded[i].permute(1,0).unsqueeze(0).data.cpu().numpy()[:, :dataset.shape[2]]*stdval + meanval #clip the padding of models  
        if align: # use Molecule Biobox class to calculate RMSD
            mol.coordinates = deepcopy(crd_ref)
            mol.set_current(0)
            mol.add_xyz(crd_mdl[0])
            rmsd = mol.rmsd(0, 1)
        else:
            rmsd = np.sqrt(np.sum((crd_ref.flatten()-crd_mdl.flatten())**2)/crd_mdl.shape[1]) # Cartesian L2 norm

        err.append(rmsd)

    return np.array(err)
    
rmsd_training = get_error(network, training_set, meanval, stdval)
csv_file_path = 'DecodedRMSDProteinHRun1.csv'

# Save the list/array to a CSV file
with open(csv_file_path, 'w', newline='') as csv_file:
    csv_writer = csv.writer(csv_file)
    csv_writer.writerows(zip(rmsd_training))

#rmsd_test = get_error(network, test_set, meanval, stdval)

100%|█████████████████████████████████████████████████████████████████████| 1427/1427 [00:00<00:00, 54146.25it/s]


Time to produce two nice violin plots, reporting on the error of training and test set. Typically the latter will be slightly higher than the former, though ideally this difference should be as small as possible, indicating that the neural network can generalize well to structures it has never seen.

### 3.2. DOPE score of input vs autoencoded <a class="anchor" id="ref32"></a>

The DOPE score is a heuristic function used to estimate the energy of a protein conformation. It is used by software like Modeller to define whether a protein model is accurate. Here, we start by defining a function calculating the DOPE score of a PDB file.

In [9]:
def dope_score(fname):
    env = Environ()
    env.libs.topology.read(file='$(LIB)/top_heav.lib')
    env.libs.parameters.read(file='$(LIB)/par.lib')
    mdl = complete_pdb(env, fname)
    atmsel = Selection(mdl.chains[0])
    score = atmsel.assess_dope()
    return score

A positive value for a DOPE score indicates that the distriution of atoms is not what one should expect from a correct protein conformation (i.e. the protein structure is bad). However, a negative DOPE score does not immediately tell us how good the structure is. To tell whether the models generated by the neural network are good, we will compare their DOPE score with the DOPE score of the input dataset, that we can assume being good. We now calculate the DOPE score of the training and test sets.

In [10]:
def get_dope(network, dataset, meanval, stdval, mol):
    
    # set residues names with protonated histidines back to generic HIS name (needed by DOPE score function)
    testH = mol.data["resname"].values
    testH[testH == "HIE"] = "HIS"
    testH[testH == "HID"] = "HIS"
    mol.data["resname"] = testH

    #z = network.encode(dataset.float())
    z = batched_encode(dataset.float())
    #decoded = network.decode(z)[:,:,:dataset.shape[2]]
    decoded = batched_decode(z, dataset.shape[2])
    
    dope_dataset = []
    dope_decoded = []
    for i in tqdm(range(dataset.shape[0])):

        # calculate DOPE score of input dataset
        crd_ref = dataset[i].permute(1,0).unsqueeze(0).data.cpu().numpy()*stdval + meanval
        mol.coordinates = deepcopy(crd_ref)
        mol.write_pdb("tmp.pdb")
        s = dope_score("tmp.pdb")
        dope_dataset.append(s)

        # calculate DOPE score of decoded counterpart
        crd_mdl = decoded[i].permute(1,0).unsqueeze(0).data.cpu().numpy()[:, :dataset.shape[2]]*stdval + meanval  
        mol.coordinates = deepcopy(crd_mdl)
        mol.write_pdb("tmp.pdb")
        s = dope_score("tmp.pdb")
        dope_decoded.append(s)
    
    return dope_dataset, dope_decoded
 
dope_training, dope_training_decoded = get_dope(network, training_set, meanval, stdval, mol)
csv_file_path = 'DecodedDOPEProteinHRun1.csv'

# Save the list/array to a CSV file
with open(csv_file_path, 'w', newline='') as csv_file:
    csv_writer = csv.writer(csv_file)
    csv_writer.writerows(zip(dope_training_decoded))
#dope_test, dope_test_decoded = get_dope(network, test_set, meanval, stdval, mol)

  0%|                                                                                   | 0/1427 [00:00<?, ?it/s]


                         MODELLER 10.4, 2022/10/28, r12463

     PROTEIN STRUCTURE MODELLING BY SATISFACTION OF SPATIAL RESTRAINTS


                     Copyright(c) 1989-2022 Andrej Sali
                            All Rights Reserved

                             Written by A. Sali
                               with help from
              B. Webb, M.S. Madhusudhan, M-Y. Shen, G.Q. Dong,
          M.A. Marti-Renom, N. Eswar, F. Alber, M. Topf, B. Oliva,
             A. Fiser, R. Sanchez, B. Yerkovich, A. Badretdinov,
                     F. Melo, J.P. Overington, E. Feyfant
                 University of California, San Francisco, USA
                    Rockefeller University, New York, USA
                      Harvard University, Cambridge, USA
                   Imperial Cancer Research Fund, London, UK
              Birkbeck College, University of London, London, UK


Kind, OS, HostName, Kernel, Processor: 4, Linux euporie 6.2.0-37-generic x86_64
Date and time of compilation 

  0%|                                                                           | 1/1427 [00:00<09:47,  2.43it/s]

read_to_681_> topology.submodel read from topology file:        3
read_pd_459W> Residue type  ACE not recognized. 'AutoModel' model building
              will treat this residue as a rigid body.
              To use real parameters, add the residue type to ${LIB}/restyp.lib,
              its topology to ${LIB}/top_*.lib, and suitable forcefield
              parameters to ${LIB}/par.lib.
rdpdb___459W> Residue type  NME not recognized. 'AutoModel' model building
              will treat this residue as a rigid body.
              To use real parameters, add the residue type to ${LIB}/restyp.lib,
              its topology to ${LIB}/top_*.lib, and suitable forcefield
              parameters to ${LIB}/par.lib.
>> Model assessment by DOPE potential
iatmcls_286W> MODEL atom not classified:  ACE:C  ACE
iatmcls_286W> MODEL atom not classified:  ACE:O  ACE
iatmcls_286W> MODEL atom not classified:  NME:N  NME
preppdf_453W> No fixed restraints selected; there may be some dynamic ones.
preppdf

  0%|                                                                           | 2/1427 [00:00<07:48,  3.04it/s]

...

read_to_681_> topology.submodel read from topology file:        3
read_pd_459W> Residue type  ACE not recognized. 'AutoModel' model building
              will treat this residue as a rigid body.
              To use real parameters, add the residue type to ${LIB}/restyp.lib,
              its topology to ${LIB}/top_*.lib, and suitable forcefield
              parameters to ${LIB}/par.lib.
rdpdb___459W> Residue type  NME not recognized. 'AutoModel' model building
              will treat this residue as a rigid body.
              To use real parameters, add the residue type to ${LIB}/restyp.lib,
              its topology to ${LIB}/top_*.lib, and suitable forcefield
              parameters to ${LIB}/par.lib.
>> Model assessment by DOPE potential
iatmcls_286W> MODEL atom not classified:  ACE:C  ACE
iatmcls_286W> MODEL atom not classified:  ACE:O  ACE
iatmcls_286W> MODEL atom not classified:  NME:N  NME
preppdf_453W> No fixed restraints selected; there may be some dynamic ones.
preppdf

100%|███████████████████████████████████████████████████████████████████████▉| 1426/1427 [06:27<00:00,  3.69it/s]

read_to_681_> topology.submodel read from topology file:        3
read_pd_459W> Residue type  ACE not recognized. 'AutoModel' model building
              will treat this residue as a rigid body.
              To use real parameters, add the residue type to ${LIB}/restyp.lib,
              its topology to ${LIB}/top_*.lib, and suitable forcefield
              parameters to ${LIB}/par.lib.
rdpdb___459W> Residue type  NME not recognized. 'AutoModel' model building
              will treat this residue as a rigid body.
              To use real parameters, add the residue type to ${LIB}/restyp.lib,
              its topology to ${LIB}/top_*.lib, and suitable forcefield
              parameters to ${LIB}/par.lib.
>> Model assessment by DOPE potential
iatmcls_286W> MODEL atom not classified:  ACE:C  ACE
iatmcls_286W> MODEL atom not classified:  ACE:O  ACE
iatmcls_286W> MODEL atom not classified:  NME:N  NME
preppdf_453W> No fixed restraints selected; there may be some dynamic ones.
preppdf

100%|████████████████████████████████████████████████████████████████████████| 1427/1427 [06:28<00:00,  3.68it/s]

read_to_681_> topology.submodel read from topology file:        3
read_pd_459W> Residue type  ACE not recognized. 'AutoModel' model building
              will treat this residue as a rigid body.
              To use real parameters, add the residue type to ${LIB}/restyp.lib,
              its topology to ${LIB}/top_*.lib, and suitable forcefield
              parameters to ${LIB}/par.lib.
rdpdb___459W> Residue type  NME not recognized. 'AutoModel' model building
              will treat this residue as a rigid body.
              To use real parameters, add the residue type to ${LIB}/restyp.lib,
              its topology to ${LIB}/top_*.lib, and suitable forcefield
              parameters to ${LIB}/par.lib.
>> Model assessment by DOPE potential
iatmcls_286W> MODEL atom not classified:  ACE:C  ACE
iatmcls_286W> MODEL atom not classified:  ACE:O  ACE
iatmcls_286W> MODEL atom not classified:  NME:N  NME
preppdf_453W> No fixed restraints selected; there may be some dynamic ones.
preppdf

---